<a href="https://colab.research.google.com/github/rineuman/Detectron2MaskRCNN/blob/master/Detectron2MaskRCNN.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Tutorial can be found here: https://medium.com/@wendeehsu/instance-segmentation-with-detectron2-127fbe01b20b

In [1]:
# Mount Google Drive for saving trained models
import os 

from google.colab import drive
drive.mount('/content/drive')

DRIVE_DIR = '/content/drive/My Drive/trained_models'

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [2]:
!pip install -U torch==1.5 torchvision==0.6 -f https://download.pytorch.org/whl/cu101/torch_stable.html
!pip install cython pyyaml==5.1
!pip install -U 'git+https://github.com/cocodataset/cocoapi.git#subdirectory=PythonAPI'
!pip install detectron2==0.1.3 -f https://dl.fbaipublicfiles.com/detectron2/wheels/cu101/index.html

Looking in links: https://download.pytorch.org/whl/cu101/torch_stable.html
Requirement already up-to-date: torch==1.5 in /usr/local/lib/python3.6/dist-packages (1.5.0+cu101)
Requirement already up-to-date: torchvision==0.6 in /usr/local/lib/python3.6/dist-packages (0.6.0+cu101)
  Cloning https://github.com/cocodataset/cocoapi.git to /tmp/pip-req-build-wpnkuv8d
  Running command git clone -q https://github.com/cocodataset/cocoapi.git /tmp/pip-req-build-wpnkuv8d
  Created wheel for pycocotools: filename=pycocotools-2.0-cp36-cp36m-linux_x86_64.whl size=266453 sha256=2db29b30782ce5f8c07341241ac58f7f4b989b6a5e67203605e15c269e9a3fca
  Stored in directory: /tmp/pip-ephem-wheel-cache-4s_5qq1t/wheels/90/51/41/646daf401c3bc408ff10de34ec76587a9b3ebfac8d21ca5c3a
Successfully built pycocotools
  Found existing installation: pycocotools 2.0
    Uninstalling pycocotools-2.0:
      Successfully uninstalled pycocotools-2.0
Looking in links: https://dl.fbaipublicfiles.com/detectron2/wheels/cu101/index.h

In [3]:
import torch, torchvision
import detectron2
from detectron2.utils.logger import setup_logger
import os
import numpy as np
import json
import cv2
from detectron2.structures import BoxMode
print(torch.__version__, torch.cuda.is_available()) # 1.5.0+cu101 True
setup_logger()

1.5.0+cu101 True


<Logger detectron2 (DEBUG)>

Parsed via_export_json to appropriate detectron2 format

In [4]:
def get_category(category_string):
  print(category_string)
  if category_string == 'door':
    print(1)
    return 1
  elif category_string == 'stair':
    print(2)
    return 2
  elif category_string == 'lift':
    print(3)
    return 3

def get_dicts(img_dir):
    json_file = os.path.join(img_dir, "via_export_json.json")
    with open(json_file) as f:
        imgs_anns = json.load(f)
    dataset_dicts = []
    for idx, v in enumerate(imgs_anns.values()):
        record = {}
        
        filename = os.path.join(img_dir, v["filename"])
        height, width = cv2.imread(filename).shape[:2]
        
        record["file_name"] = filename
        record["image_id"] = idx
        record["height"] = height
        record["width"] = width
      
        annos = v["regions"]
        print("Annotationen:")
        print(annos)

        objs = []
        for anno in annos:
            polygons = anno["shape_attributes"]
            barriers = anno["region_attributes"]
            print("Polygons: ")
            print(polygons)
            print("Barriers: ")
            print(barriers)
            if polygons['name'] == 'polygon':
              px = polygons["all_points_x"]
              py = polygons["all_points_y"]
              poly = [(x + 0.5, y + 0.5) for x, y in zip(px, py)]
              poly = [p for x in poly for p in x]
              category = get_category(barriers.get("barrier"))
              obj = {
                  "bbox": [np.min(px), np.min(py), np.max(px), np.max(py)],
                  "bbox_mode": BoxMode.XYXY_ABS,
                  "segmentation": [poly],
                  "category_id": category,
                  "iscrowd": 0
                  }
              objs.append(obj)
              print(objs)
            elif polygons['name'] == 'rect':
              px = [polygons['x'], polygons['x'] + polygons['width']]
              py = [polygons['y'], polygons['y'] + polygons['height']]
              poly = [(x + 0.5, y + 0.5) for x, y in zip(px, py)]
              poly = [p for x in poly for p in x]
              category = get_category(barriers.get("barrier"))

              obj = {
                  "bbox": [np.min(px), np.min(py), np.max(px), np.max(py)],
                  "bbox_mode": BoxMode.XYXY_ABS,
                  "segmentation": [poly],
                  "category_id": category,
                  "iscrowd": 0
                  }
              objs.append(obj)
              print(objs)
            elif polygons['name'] == 'circle':
              px = [polygons['cx'] - polygons['r'] , polygons['cx'] + polygons['r']]
              py = [polygons['cy'] - polygons['r'] , polygons['cy'] + polygons['r']]
              poly = [(x + 0.5, y + 0.5) for x, y in zip(px, py)]
              poly = [p for x in poly for p in x]
              category = get_category(barriers.get("barrier"))

              obj = {
                  "bbox": [np.min(px), np.min(py), np.max(px), np.max(py)],
                  "bbox_mode": BoxMode.XYXY_ABS,
                  "segmentation": [poly],
                  "category_id": category,
                  "iscrowd": 0
                  }
              objs.append(obj)
              print(objs)

            
        record["annotations"] = objs
        dataset_dicts.append(record)
    return dataset_dicts

Register custom training set

In [5]:
# Root directory of the project
ROOT_DIR = os.path.abspath("../")

In [6]:
!git clone https://github.com/rineuman/newDataSet.git

fatal: destination path 'newDataSet' already exists and is not an empty directory.


In [7]:
from detectron2.data import DatasetCatalog, MetadataCatalog
path = "/content/newDataSet/" # path to your image folder
for d in ["train", "val"]:
    DatasetCatalog.register("barrier_" + d, lambda d=d: get_dicts(path + "/" +  d))
    MetadataCatalog.get("barrier_" + d).set(thing_classes=["barrier"])

Check if data can be loaded

In [8]:
import random
from google.colab.patches import cv2_imshow
from detectron2.utils.visualizer import Visualizer
dataset_dicts = get_dicts(path + "train")
for d in random.sample(dataset_dicts, 3):
    img = cv2.imread(d["file_name"])
    visualizer = Visualizer(img[:, :, ::-1], metadata=MetadataCatalog.get("barrier_train"), scale=0.5)
    vis = visualizer.draw_dataset_dict(d)
    cv2_imshow(vis.get_image()[:, :, ::-1])

Annotationen:
[{'shape_attributes': {'name': 'rect', 'x': 464, 'y': 354, 'width': 111, 'height': 59}, 'region_attributes': {'barrier': 'door'}}, {'shape_attributes': {'name': 'rect', 'x': 12, 'y': 153, 'width': 76, 'height': 47}, 'region_attributes': {'barrier': 'stair'}}, {'shape_attributes': {'name': 'rect', 'x': 223, 'y': 354, 'width': 109, 'height': 58}, 'region_attributes': {'barrier': 'door'}}, {'shape_attributes': {'name': 'rect', 'x': 1793, 'y': 1125, 'width': 55, 'height': 40}, 'region_attributes': {'barrier': 'stair'}}, {'shape_attributes': {'name': 'rect', 'x': 1793, 'y': 1088, 'width': 30, 'height': 24}, 'region_attributes': {'barrier': 'stair'}}]
Polygons: 
{'name': 'rect', 'x': 464, 'y': 354, 'width': 111, 'height': 59}
Barriers: 
{'barrier': 'door'}
door
1
[{'bbox': [464, 354, 575, 413], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[464.5, 354.5, 575.5, 413.5]], 'category_id': 1, 'iscrowd': 0}]
Polygons: 
{'name': 'rect', 'x': 12, 'y': 153, 'width': 76, 'height':

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




{'barrier': 'door'}
door
1
[{'bbox': [1532, 508, 1550, 529], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[1532.5, 508.5, 1550.5, 529.5]], 'category_id': 1, 'iscrowd': 0}, {'bbox': [1432, 553, 1455, 572], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[1432.5, 553.5, 1455.5, 572.5]], 'category_id': 1, 'iscrowd': 0}, {'bbox': [1441, 583, 1460, 598], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[1441.5, 583.5, 1460.5, 598.5]], 'category_id': 1, 'iscrowd': 0}, {'bbox': [1440, 604, 1458, 623], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[1440.5, 604.5, 1458.5, 623.5]], 'category_id': 1, 'iscrowd': 0}, {'bbox': [1420, 684, 1441, 700], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[1420.5, 684.5, 1441.5, 700.5]], 'category_id': 1, 'iscrowd': 0}, {'bbox': [1524, 646, 1540, 665], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[1524.5, 646.5, 1540.5, 665.5]], 'category_id': 1, 'iscrowd': 0}, {'bbox': [1596, 645, 1611, 664], 'bbox_mode': <BoxMode.XYXY

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




Polygons: 
{'name': 'rect', 'x': 1456, 'y': 2367, 'width': 44, 'height': 25}
Barriers: 
{'barrier': 'stair'}
stair
2
[{'bbox': [66, 520, 84, 548], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[66.5, 520.5, 84.5, 548.5]], 'category_id': 1, 'iscrowd': 0}, {'bbox': [90, 553, 105, 567], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[90.5, 553.5, 105.5, 567.5]], 'category_id': 1, 'iscrowd': 0}, {'bbox': [149, 549, 168, 567], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[149.5, 549.5, 168.5, 567.5]], 'category_id': 1, 'iscrowd': 0}, {'bbox': [211, 549, 226, 568], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[211.5, 549.5, 226.5, 568.5]], 'category_id': 1, 'iscrowd': 0}, {'bbox': [271, 554, 286, 569], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[271.5, 554.5, 286.5, 569.5]], 'category_id': 1, 'iscrowd': 0}, {'bbox': [330, 550, 347, 568], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[330.5, 550.5, 347.5, 568.5]], 'category_id': 1, 'iscrowd': 0},

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




Polygons: 
{'name': 'polygon', 'all_points_x': [1023, 1019, 973, 987, 1035], 'all_points_y': [489, 492, 494, 528, 542]}
Barriers: 
{'barrier': 'door'}
door
1
[{'bbox': [1301, 1847, 1341, 1897], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[1301.5, 1860.5, 1303.5, 1858.5, 1312.5, 1897.5, 1341.5, 1889.5, 1333.5, 1847.5]], 'category_id': 2, 'iscrowd': 0}, {'bbox': [1360, 1885, 1420, 1922], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[1360.5, 1895.5, 1416.5, 1885.5, 1420.5, 1918.5, 1360.5, 1922.5]], 'category_id': 2, 'iscrowd': 0}, {'bbox': [1404, 1835, 1445, 1876], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[1404.5, 1841.5, 1437.5, 1835.5, 1445.5, 1874.5, 1414.5, 1876.5]], 'category_id': 2, 'iscrowd': 0}, {'bbox': [1073, 2109, 1161, 2178], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[1073.5, 2142.5, 1140.5, 2109.5, 1161.5, 2144.5, 1088.5, 2178.5]], 'category_id': 2, 'iscrowd': 0}, {'bbox': [1096, 2167, 1176, 2213], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, '

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'barrier': 'door'}
door
1
[{'bbox': [2102, 65, 2165, 261], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[2102.5, 65.5, 2165.5, 261.5]], 'category_id': 2, 'iscrowd': 0}, {'bbox': [2038, 109, 2100, 182], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[2038.5, 109.5, 2100.5, 182.5]], 'category_id': 2, 'iscrowd': 0}, {'bbox': [956, 709, 1001, 803], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[956.5, 709.5, 1001.5, 803.5]], 'category_id': 2, 'iscrowd': 0}, {'bbox': [1010, 700, 1055, 747], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[1010.5, 700.5, 1055.5, 747.5]], 'category_id': 2, 'iscrowd': 0}, {'bbox': [892, 551, 941, 638], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[892.5, 551.5, 941.5, 638.5]], 'category_id': 1, 'iscrowd': 0}, {'bbox': [901, 794, 941, 859], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'segmentation': [[901.5, 794.5, 941.5, 859.5]], 'category_id': 1, 'iscrowd': 0}, {'bbox': [1068, 863, 1150, 922], 'bbox_mode': <BoxMode.XYXY_ABS: 0>, 'se

IndexError: ignored

Training


In [ ]:
from detectron2.engine import DefaultTrainer
from detectron2.config import get_cfg
from detectron2 import model_zoo
from detectron2.engine import DefaultPredictor
cfg = get_cfg()
cfg.OUTPUT_DIR = DRIVE_DIR
cfg.merge_from_file(model_zoo.get_config_file("COCO-InstanceSegmentation/mask_rcnn_R_50_FPN_3x.yaml"))

In [ ]:
cfg.DATASETS.TRAIN = ("barrier_train",)     # our training dataset
cfg.DATASETS.TEST = ()
cfg.DATALOADER.NUM_WORKERS = 2     # number of parallel data loading workers
cfg.MODEL.WEIGHTS = model_zoo.get_checkpoint_url("COCO-InstanceSegmentation/mask_rcnn_R_50_FPN_3x.yaml")     # use pretrained weights
cfg.SOLVER.IMS_PER_BATCH = 2     # in 1 iteration the model sees 2 images
cfg.SOLVER.BASE_LR = 0.00025     # learning rate
cfg.SOLVER.MAX_ITER = 450        # number of iteration
cfg.MODEL.ROI_HEADS.BATCH_SIZE_PER_IMAGE = 128     # number of proposals to sample for training
cfg.MODEL.ROI_HEADS.NUM_CLASSES = 3  # only has one class (mango)
os.makedirs(cfg.OUTPUT_DIR, exist_ok=True)
trainer = DefaultTrainer(cfg)
trainer.resume_or_load(resume=False)
trainer.train()

In [ ]:
# Look at training curves in tensorboard:
%load_ext tensorboard
%tensorboard --logdir DRIVE_DIR

In [ ]:
cfg.MODEL.WEIGHTS = os.path.join(cfg.OUTPUT_DIR, "model_final.pth")
cfg.MODEL.ROI_HEADS.SCORE_THRESH_TEST = 0.7   # set the testing threshold for this model
cfg.DATASETS.TEST = ("barrier_val", )
predictor = DefaultPredictor(cfg)

In [ ]:
from detectron2.utils.visualizer import ColorMode
dataset_dicts = get_dicts(path + "val")
for d in dataset_dicts:    
    im = cv2.imread(d["file_name"])
    outputs = predictor(im)
    v = Visualizer(im[:, :, ::-1],
                   metadata=MetadataCatalog.get("barrier_train"), 
                   scale=0.8, 
                   instance_mode=ColorMode.IMAGE_BW   # remove the colors of unsegmented pixels
    )
    v = v.draw_instance_predictions(outputs["instances"].to("cpu"))
    cv2_imshow(v.get_image()[:, :, ::-1])

In [ ]:
import pickle
filename = os.path.join(DRIVE_DIR, "config.pkl")
print(filename)
with open(filename, 'wb') as f:
     pickle.dump(cfg, f)